### This notebook is to replicate data gathering techniques used in `steam-data` project by @CraigKelly

In [1]:
"""Create idlist.csv."""

import csv
import requests


def idreader():
    """Get all ID's from Steam."""
    URL = "http://api.steampowered.com/ISteamApps/GetAppList/v2"
    print("GET", URL)
    data = requests.get(URL).json()
    for a in data.get("applist", dict()).get("apps", dict()):
        appid = a.get('appid', None)
        name = a.get('name', '')
        if not appid:
            print("Skipping mising appid: %s" % repr(a))
            continue
        if not name:
            print("AUDIT: missing name in record: %s" % repr(a))
        yield appid, name


"""Entry point."""
print("Creating idlist.csv")
with open("idlist.csv", "w") as basefile:
    writer = csv.writer(basefile)
    writer.writerow(["ID", "Name"])
    count = 0
    for appid, name in idreader():
        writer.writerow([appid, name])
        count += 1
print("ID Records Written: %d" % count)

Creating idlist.csv
GET http://api.steampowered.com/ISteamApps/GetAppList/v2
AUDIT: missing name in record: {'appid': 1118314, 'name': ''}
ID Records Written: 114811


In [3]:
"""Entry point."""
logging.basicConfig(level=logging.DEBUG)
logging.getLogger('requests').setLevel(logging.DEBUG)
log = logging.getLogger('games')

defaults = {
    'cc': 'US',
    'l': 'english',
    'v': '1',
}
log.info("Default parameters: %s", repr(defaults))

URL = "http://store.steampowered.com/api/appdetails/"
LIMIT = 150
WAIT_TIME = (5 * 60) + 10  # 5 minutes plus a cushion

INFO:games:Default parameters: {'cc': 'US', 'l': 'english', 'v': '1'}


In [5]:
previous_results()

set()

In [6]:
with open("games.json", "a") as f:
    count, batch_count = 0, 0

    log.info("Opening idlist.csv")
    for appid, appname in id_reader():
        if appid in previous_results():
            log.info("Skipping previously found id %d", appid)
            continue

        req_data = dict(defaults)
        req_data['appids'] = str(appid)

        resp_data = requests.get(URL, params=req_data)

        # Loop is an artifact of Steam's past suppot for multiple appid
        # queries: we use it to insure we got back what we asked for - the
        # details for appid
        for result_appid, game in resp_data.json().items():
            if parse_id(result_appid) != appid:
                log.error("Invalid - %s does not match requested id %d", result_appid, appid)

            game['query_appid'] = appid
            game['query_appname'] = appname
            f.write(json.dumps(game) + '\n')

            count += 1

        batch_count += 1
        if batch_count >= LIMIT:
            log.info("batch count is %d, waiting for %d secs", batch_count, WAIT_TIME)
            time.sleep(WAIT_TIME)
            batch_count = 0

log.info("Game records written: %d", count)


INFO:games:Opening idlist.csv
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): store.steampowered.com:80
DEBUG:urllib3.connectionpool:http://store.steampowered.com:80 "GET /api/appdetails/?cc=US&l=english&v=1&appids=216938 HTTP/1.1" 302 138
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): store.steampowered.com:443
DEBUG:urllib3.connectionpool:https://store.steampowered.com:443 "GET /api/appdetails/?cc=US&l=english&v=1&appids=216938 HTTP/1.1" 200 48
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): store.steampowered.com:80
DEBUG:urllib3.connectionpool:http://store.steampowered.com:80 "GET /api/appdetails/?cc=US&l=english&v=1&appids=660010 HTTP/1.1" 302 138
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): store.steampowered.com:443
DEBUG:urllib3.connectionpool:https://store.steampowered.com:443 "GET /api/appdetails/?cc=US&l=english&v=1&appids=660010 HTTP/1.1" 200 48
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): s

DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): store.steampowered.com:80
DEBUG:urllib3.connectionpool:http://store.steampowered.com:80 "GET /api/appdetails/?cc=US&l=english&v=1&appids=1358760 HTTP/1.1" 302 138
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): store.steampowered.com:443
DEBUG:urllib3.connectionpool:https://store.steampowered.com:443 "GET /api/appdetails/?cc=US&l=english&v=1&appids=1358760 HTTP/1.1" 200 2927
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): store.steampowered.com:80
DEBUG:urllib3.connectionpool:http://store.steampowered.com:80 "GET /api/appdetails/?cc=US&l=english&v=1&appids=1358800 HTTP/1.1" 302 138
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): store.steampowered.com:443
DEBUG:urllib3.connectionpool:https://store.steampowered.com:443 "GET /api/appdetails/?cc=US&l=english&v=1&appids=1358800 HTTP/1.1" 200 2772
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): store.steampowered.com:

DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): store.steampowered.com:80
DEBUG:urllib3.connectionpool:http://store.steampowered.com:80 "GET /api/appdetails/?cc=US&l=english&v=1&appids=1358162 HTTP/1.1" 302 138
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): store.steampowered.com:443
DEBUG:urllib3.connectionpool:https://store.steampowered.com:443 "GET /api/appdetails/?cc=US&l=english&v=1&appids=1358162 HTTP/1.1" 200 49
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): store.steampowered.com:80
DEBUG:urllib3.connectionpool:http://store.steampowered.com:80 "GET /api/appdetails/?cc=US&l=english&v=1&appids=1358180 HTTP/1.1" 302 138
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): store.steampowered.com:443
DEBUG:urllib3.connectionpool:https://store.steampowered.com:443 "GET /api/appdetails/?cc=US&l=english&v=1&appids=1358180 HTTP/1.1" 200 1635
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): store.steampowered.com:80

DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): store.steampowered.com:80
DEBUG:urllib3.connectionpool:http://store.steampowered.com:80 "GET /api/appdetails/?cc=US&l=english&v=1&appids=1357580 HTTP/1.1" 302 138
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): store.steampowered.com:443
DEBUG:urllib3.connectionpool:https://store.steampowered.com:443 "GET /api/appdetails/?cc=US&l=english&v=1&appids=1357580 HTTP/1.1" 200 2650
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): store.steampowered.com:80
DEBUG:urllib3.connectionpool:http://store.steampowered.com:80 "GET /api/appdetails/?cc=US&l=english&v=1&appids=1357590 HTTP/1.1" 302 138
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): store.steampowered.com:443
DEBUG:urllib3.connectionpool:https://store.steampowered.com:443 "GET /api/appdetails/?cc=US&l=english&v=1&appids=1357590 HTTP/1.1" 200 2702
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): store.steampowered.com:

DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): store.steampowered.com:80
DEBUG:urllib3.connectionpool:http://store.steampowered.com:80 "GET /api/appdetails/?cc=US&l=english&v=1&appids=1357930 HTTP/1.1" 302 138
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): store.steampowered.com:443
DEBUG:urllib3.connectionpool:https://store.steampowered.com:443 "GET /api/appdetails/?cc=US&l=english&v=1&appids=1357930 HTTP/1.1" 200 1993
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): store.steampowered.com:80
DEBUG:urllib3.connectionpool:http://store.steampowered.com:80 "GET /api/appdetails/?cc=US&l=english&v=1&appids=1357940 HTTP/1.1" 302 138
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): store.steampowered.com:443
DEBUG:urllib3.connectionpool:https://store.steampowered.com:443 "GET /api/appdetails/?cc=US&l=english&v=1&appids=1357940 HTTP/1.1" 200 2714
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): store.steampowered.com:

...

DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): store.steampowered.com:80
DEBUG:urllib3.connectionpool:http://store.steampowered.com:80 "GET /api/appdetails/?cc=US&l=english&v=1&appids=669960 HTTP/1.1" 302 138
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): store.steampowered.com:443
DEBUG:urllib3.connectionpool:https://store.steampowered.com:443 "GET /api/appdetails/?cc=US&l=english&v=1&appids=669960 HTTP/1.1" 200 2852
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): store.steampowered.com:80
DEBUG:urllib3.connectionpool:http://store.steampowered.com:80 "GET /api/appdetails/?cc=US&l=english&v=1&appids=669970 HTTP/1.1" 302 138
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): store.steampowered.com:443
DEBUG:urllib3.connectionpool:https://store.steampowered.com:443 "GET /api/appdetails/?cc=US&l=english&v=1&appids=669970 HTTP/1.1" 200 1868
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): store.steampowered.com:80
D

DEBUG:urllib3.connectionpool:http://store.steampowered.com:80 "GET /api/appdetails/?cc=US&l=english&v=1&appids=669190 HTTP/1.1" 302 138
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): store.steampowered.com:443
DEBUG:urllib3.connectionpool:https://store.steampowered.com:443 "GET /api/appdetails/?cc=US&l=english&v=1&appids=669190 HTTP/1.1" 200 1825
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): store.steampowered.com:80
DEBUG:urllib3.connectionpool:http://store.steampowered.com:80 "GET /api/appdetails/?cc=US&l=english&v=1&appids=669200 HTTP/1.1" 302 138
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): store.steampowered.com:443
DEBUG:urllib3.connectionpool:https://store.steampowered.com:443 "GET /api/appdetails/?cc=US&l=english&v=1&appids=669200 HTTP/1.1" 200 1550
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): store.steampowered.com:80
DEBUG:urllib3.connectionpool:http://store.steampowered.com:80 "GET /api/appdetails/?cc=US&

DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): store.steampowered.com:443
DEBUG:urllib3.connectionpool:https://store.steampowered.com:443 "GET /api/appdetails/?cc=US&l=english&v=1&appids=669580 HTTP/1.1" 200 3068
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): store.steampowered.com:80
DEBUG:urllib3.connectionpool:http://store.steampowered.com:80 "GET /api/appdetails/?cc=US&l=english&v=1&appids=669590 HTTP/1.1" 302 138
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): store.steampowered.com:443
DEBUG:urllib3.connectionpool:https://store.steampowered.com:443 "GET /api/appdetails/?cc=US&l=english&v=1&appids=669590 HTTP/1.1" 200 1899
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): store.steampowered.com:80
DEBUG:urllib3.connectionpool:http://store.steampowered.com:80 "GET /api/appdetails/?cc=US&l=english&v=1&appids=668680 HTTP/1.1" 302 138
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): store.steampowered.com:443

DEBUG:urllib3.connectionpool:https://store.steampowered.com:443 "GET /api/appdetails/?cc=US&l=english&v=1&appids=668910 HTTP/1.1" 200 2923
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): store.steampowered.com:80
DEBUG:urllib3.connectionpool:http://store.steampowered.com:80 "GET /api/appdetails/?cc=US&l=english&v=1&appids=668950 HTTP/1.1" 302 138
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): store.steampowered.com:443
DEBUG:urllib3.connectionpool:https://store.steampowered.com:443 "GET /api/appdetails/?cc=US&l=english&v=1&appids=668950 HTTP/1.1" 502 12346


JSONDecodeError: Unexpected UTF-8 BOM (decode using utf-8-sig): line 1 column 1 (char 0)

In [2]:
import csv
import json
import time
import requests
import logging


def parse_id(i):
    """Since we deal with both strings and ints, force appid to be correct."""
    try:
        return int(str(i).strip())
    except:
        return None


def id_reader():
    """Read the previous created idlist.csv."""
    with open("idlist.csv") as basefile:
        reader = csv.DictReader(basefile)
        for row in reader:
            yield parse_id(row['ID']), row['Name']


def previous_results():
    """Return a set of all previous found ID's."""
    all_ids = set()
    with open("games.json") as f:
        for line in f:
            rec = json.loads(line)
            appid = parse_id(rec.get('query_appid', None))
            if appid:
                all_ids.add(appid)
    return all_ids


def main():
    """Entry point."""
    logging.basicConfig(level=logging.DEBUG)
    logging.getLogger('requests').setLevel(logging.DEBUG)
    log = logging.getLogger('games')

    defaults = {
        'cc': 'US',
        'l': 'english',
        'v': '1',
    }
    log.info("Default parameters: %s", repr(defaults))

    URL = "http://store.steampowered.com/api/appdetails/"
    LIMIT = 150
    WAIT_TIME = (5 * 60) + 10  # 5 minutes plus a cushion

    log.info("Getting previous results from games.json")
    previos_ids = previous_results()

    log.info("Opening games.json")
    with open("games.json", "a") as f:
        count, batch_count = 0, 0

        log.info("Opening idlist.csv")
        for appid, appname in id_reader():
            if appid in previos_ids:
                log.info("Skipping previously found id %d", appid)
                continue

            req_data = dict(defaults)
            req_data['appids'] = str(appid)

            resp_data = requests.get(URL, params=req_data)

            # Loop is an artifact of Steam's past suppot for multiple appid
            # queries: we use it to insure we got back what we asked for - the
            # details for appid
            for result_appid, game in resp_data.json().items():
                if parse_id(result_appid) != appid:
                    log.error("Invalid - %s does not match requested id %d", result_appid, appid)

                game['query_appid'] = appid
                game['query_appname'] = appname
                f.write(json.dumps(game) + '\n')

                count += 1

            batch_count += 1
            if batch_count >= LIMIT:
                log.info("batch count is %d, waiting for %d secs", batch_count, WAIT_TIME)
                time.sleep(WAIT_TIME)
                batch_count = 0

    log.info("Game records written: %d", count)


if __name__ == "__main__":
    main()

INFO:games:Default parameters: {'cc': 'US', 'l': 'english', 'v': '1'}
INFO:games:Getting previous results from games.json


FileNotFoundError: [Errno 2] No such file or directory: 'games.json'

In [7]:
# games.json is trouble (takes a long time to fetch data and prone to errors)
# Let's see how to get data from this file:
import json


def read_games():
    """Simple generator to yield everything in games.json as Python dicts."""
    with open("games.json") as f:
        for line in f:
            if not line:
                continue
            rec = json.loads(line)
            if not rec.get('success', None):
                continue
            if 'game' != rec.get('data', {}).get('type', ''):
                continue

            yield rec


def main():
    """Entry point - main logic."""
    good, bad, error, total = 0, 0, 0, 0

    for game in read_games():
        total += 1
        d = game.get("data", None)
        if d is None:
            error += 1
        elif d.get('type', None):
            good += 1
        else:
            bad += 1

    print("Good Records Seen:  %8d" % good)
    print("Bad Records Seen:   %8d" % bad)
    print("Error Records Seen: %8d" % error)
    print("                    --------")
    print("Total Records Seen: %8d" % total)
    print("                    --------")
    print("Sanity Check Total: %8d" % (good+bad+error,))

if __name__ == "__main__":
    main()

Good Records Seen:      9680
Bad Records Seen:          0
Error Records Seen:        0
                    --------
Total Records Seen:     9680
                    --------
Sanity Check Total:     9680


In [10]:
#!/usr/env/bin python

# pylama:ignore=E501,C901

"""Create games-features.csv from games.json."""

import csv
import json
import re
import html

from unidecode import unidecode


def game_reader():
    """Simple generator to yield everything in games.json as Python dicts."""
    with open("games.json") as f:
        for line in f:
            if not line:
                continue
            rec = json.loads(line)
            if not rec.get('success', None):
                continue
            if 'game' != rec.get('data', {}).get('type', ''):
                continue

            yield rec


html_tags = re.compile('<[^<]+?>')


def txt(t, defval=' '):
    """Return filtered text."""
    # Ascii-compatible UTF8 string
    s = unidecode(str(t)).strip()
    # s = unicodedata.normalize('NFKD', str(t)).encode('ascii', 'ignore').decode('utf-8')
    # No html tags
    s = html_tags.sub('', s)
    # No unescape any html entities (like &gt; or &quot;)
    s = html.unescape(s)
    # And now we need to kill any HTML tags we re-introduced
    s = html_tags.sub('', s)
    # And finally kill any troublesome characters
    for c in ",'\"\r\n\t":
        s = s.replace(c, '')
    return s.strip() or defval


def num(s, defval=0):
    """Return correctly interpreted number (current assume ints)."""
    n = str(s).strip() if s else None
    if not n:
        return defval
    try:
        return int(n)
    except:
        print("Could not int(%s)" % (n,))
        return defval


def numf(s, defval=0.0):
    """Return interpreted float - unlike num default is 0.0."""
    f = str(s).strip() if s else None
    if not f:
        return defval
    try:
        return float(f)
    except:
        print("Could not float(%s)" % (f,))
        return defval


def txt_count(lst):
    """Return count of unique, non-empty strings in the list/iterable."""
    uniq = set([str(i).strip().lower() for i in lst])
    return len(uniq - set(['']))


# List of columns in the order we want them in the file
# If you change the function `record`, you probably want to change
# this list
COLUMNS = [
    # Identifying fields
    "QueryID", "ResponseID", "QueryName", "ResponseName", "ReleaseDate",

    # Numerics
    "RequiredAge",
    "DemoCount",
    "DeveloperCount",
    "DLCCount",
    "Metacritic",
    "MovieCount",
    "PackageCount",
    "RecommendationCount",
    "PublisherCount",
    "ScreenshotCount",

    # Numerics from SteamSpy JSON
    "SteamSpyOwners",
    "SteamSpyOwnersVariance",
    "SteamSpyPlayersEstimate",
    "SteamSpyPlayersVariance",

    # Achievements (numeric)
    "AchievementCount", "AchievementHighlightedCount",

    # Bools
    "ControllerSupport",
    "IsFree",
    "FreeVerAvail", "PurchaseAvail", "SubscriptionAvail",
    "PlatformWindows", "PlatformLinux", "PlatformMac",

    # Requirements (bool)
    "PCReqsHaveMin", "PCReqsHaveRec",
    "LinuxReqsHaveMin", "LinuxReqsHaveRec",
    "MacReqsHaveMin", "MacReqsHaveRec",

    # Categories (bool)
    "CategorySinglePlayer", "CategoryMultiplayer", "CategoryCoop", "CategoryMMO",
    "CategoryInAppPurchase",
    "CategoryIncludeSrcSDK", "CategoryIncludeLevelEditor",
    "CategoryVRSupport",

    # Genres (bool)
    "GenreIsNonGame",
    "GenreIsIndie", "GenreIsAction", "GenreIsAdventure", "GenreIsCasual",
    "GenreIsStrategy", "GenreIsRPG", "GenreIsSimulation", "GenreIsEarlyAccess",
    "GenreIsFreeToPlay", "GenreIsSports", "GenreIsRacing",
    "GenreIsMassivelyMultiplayer",

    # Pricing
    "PriceCurrency", "PriceInitial", "PriceFinal",

    # Text fields (potentially long)
    "SupportEmail",
    "SupportURL",
    "AboutText",
    "Background",
    "ShortDescrip",
    "DetailedDescrip",
    "DRMNotice",
    "ExtUserAcctNotice",
    "HeaderImage",
    "LegalNotice",
    "Reviews",
    "SupportedLanguages",
    "Website",
    "PCMinReqsText",
    "PCRecReqsText",
    "LinuxMinReqsText",
    "LinuxRecReqsText",
    "MacMinReqsText",
    "MacRecReqsText",
]


def steam_spy_read(appid, *field_names):
    """Read the given fields from steam spy JSON."""
    if not steam_spy_read.steam_spy:
        with open("steamspy.json") as inp:
            steam_spy_read.steam_spy = json.load(inp)
        if not steam_spy_read.steam_spy:
            raise Exception("Could not read steamspy.json")

    rec = steam_spy_read.steam_spy.get(str(appid), dict())
    return tuple([num(rec.get(f, 0)) for f in field_names])


steam_spy_read.steam_spy = dict()


def record(raw):
    """Convert the raw JSON dict to our CSV record."""
    data = raw["data"]

    # Categories
    cats = set()
    for d in data.get('categories', []):
        c = d.get('description', '').strip().lower()
        if c:
            cats.add(c)

    # Genres
    genres = set()
    non_game_genres = set([
        "utilities", "design & illustration", "animation & modeling",
        "software training", "education", "audio production",
        "video production", "web publishing", "photo editing", "accounting",
    ])
    for d in data.get('genres', []):
        g = d.get('description', '').strip().lower()
        if g:
            if g in non_game_genres:
                genres.add('nongame')
            else:
                genres.add(g)

    # Package groups
    pgs = data.get("package_groups", [])
    pg_free, pg_purchase, pg_subscript = False, False, False
    for pg in pgs:
        if pg.get('is_recurring_subscription', '') == 'true':
            pg_subscript = True
        for s in pg.get('subs', list()):
            if s.get('is_free_license', None):
                pg_free = True
            elif s.get('price_in_cents_with_discount', 0) > 0:
                pg_purchase = True

    # Requirements
    # The extra "or {}" check is because some empty requirements get interpreted
    # as an empty list...
    linux_req = data.get('linux_requirements', {}) or {}
    mac_req = data.get('mac_requirements', {}) or {}
    pc_req = data.get('pc_requirements', {}) or {}

    # SteamSpy.com owner/player data
    ss_owners, ss_owners_var, ss_players, ss_players_var = steam_spy_read(
        raw['query_appid'],
        'owners',
        'owners_variance',
        'players_forever',
        'players_forever_variance',
    )

    return {
        "QueryID": raw['query_appid'],

        # Text fields
        "QueryName": raw['query_appname'],
        "ResponseName": txt(data.get('name', '')),
        "AboutText": txt(data.get('about_the_game', '')),
        "Background": txt(data.get('background', '')),
        "ShortDescrip": txt(data.get('short_description', '')),
        "DetailedDescrip": txt(data.get('detailed_description', '')),
        "DRMNotice": txt(data.get('drm_notice', '')),
        "ExtUserAcctNotice": txt(data.get('ext_user_account_notice', '')),
        "HeaderImage": txt(data.get('header_image', '')),
        "LegalNotice": txt(data.get('legal_notice', '')),
        "Reviews": txt(data.get('reviews', '')),
        "SupportedLanguages": txt(data.get('supported_languages', '')),
        "Website": txt(data.get('website', '')),
        "ReleaseDate": txt(data.get('release_date', {}).get('date', '')),
        "SupportEmail": txt(data.get('support_info', {}).get('email', '')),
        "SupportURL": txt(data.get('support_info', {}).get('url', '')),

        # Numeric fields
        "ResponseID": num(data.get('steam_appid', None)),
        "RequiredAge": num(data.get('required_age', None)),
        "DemoCount": txt_count(data.get('demos', [])),
        "DeveloperCount": txt_count(data.get('developers', [])),
        "DLCCount": txt_count(data.get('dlc', [])),
        "Metacritic": num(data.get('metacritic', {}).get('score', '')),
        "MovieCount": txt_count([num(d.get('id', '')) for d in data.get('movies', [])]),
        "PackageCount": txt_count(data.get('packages', [])),
        "PublisherCount": txt_count(data.get('publishers', [])),
        "RecommendationCount": num(data.get('recommendations', {}).get('total', 0)),
        "ScreenshotCount": txt_count(data.get('screenshots', [])),

        # Steam Spy numeric fields
        "SteamSpyOwners": ss_owners,
        "SteamSpyOwnersVariance": ss_owners_var,
        "SteamSpyPlayersEstimate": ss_players,
        "SteamSpyPlayersVariance": ss_players_var,

        # Achivements
        "AchievementCount": num(data.get('achievements', {}).get('total', 0)),
        "AchievementHighlightedCount": txt_count(data.get('achievements', {}).get('highlighted', [])),

        # "Easy" Boolean fields
        "ControllerSupport": data.get("controller_support", "").strip().lower() == "full",
        "IsFree": data.get("is_free", False),
        "FreeVerAvail": pg_free,
        "PurchaseAvail": pg_purchase,
        "SubscriptionAvail": pg_subscript,
        "PlatformWindows": data.get("platforms", {}).get("windows", False),
        "PlatformLinux": data.get("platforms", {}).get("linux", False),
        "PlatformMac": data.get("platforms", {}).get("mac", False),

        # Categories (Bool)
        "CategoryMultiplayer": any(i in cats for i in [
            "cross-platform multiplayer", "local multi-player", "multi-player",
            "online multi-player", "shared/split screen"
        ]),
        "CategoryCoop": any(i in cats for i in [
            "co-op", "local co-op", "online co-op"
        ]),
        "CategoryInAppPurchase": "in-app purchases" in cats,
        "CategoryIncludeSrcSDK": "includes source sdk" in cats,
        "CategoryIncludeLevelEditor": "includes level editor" in cats,
        "CategoryMMO": "mmo" in cats,
        "CategorySinglePlayer": "single-player" in cats,
        "CategoryVRSupport": "vr support" in cats,

        # Genres (Bool)
        "GenreIsNonGame": "nongame" in genres,
        "GenreIsIndie": "indie" in genres,
        "GenreIsAction": "action" in genres,
        "GenreIsAdventure": "adventure" in genres,
        "GenreIsCasual": "casual" in genres,
        "GenreIsStrategy": "strategy" in genres,
        "GenreIsRPG": "rpg" in genres,
        "GenreIsSimulation": "simulation" in genres,
        "GenreIsEarlyAccess": "early access" in genres,
        "GenreIsFreeToPlay": "free to play" in genres,
        "GenreIsSports": "sports" in genres,
        "GenreIsRacing": "racing" in genres,
        "GenreIsMassivelyMultiplayer": "massively multiplayer" in genres,

        # Requirements (Bool)
        "LinuxReqsHaveMin": True if linux_req.get('minimum', '') else False,
        "LinuxReqsHaveRec": True if linux_req.get('recommended', '') else False,
        "MacReqsHaveMin": True if mac_req.get('minimum', '') else False,
        "MacReqsHaveRec": True if mac_req.get('recommended', '') else False,
        "PCReqsHaveMin": True if pc_req.get('minimum', '') else False,
        "PCReqsHaveRec": True if pc_req.get('recommended', '') else False,

        # Requirements (Text)
        "PCMinReqsText": txt(pc_req.get('minimum', '')),
        "PCRecReqsText": txt(pc_req.get('recommended', '')),
        "LinuxMinReqsText": txt(linux_req.get('minimum', '')),
        "LinuxRecReqsText": txt(linux_req.get('recommended', '')),
        "MacMinReqsText": txt(mac_req.get('minimum', '')),
        "MacRecReqsText": txt(mac_req.get('recommended', '')),

        # Pricing (prices are in pennies and we convert to dollars)
        "PriceCurrency": txt(data.get("price_overview", {}).get("currency", "")),
        "PriceInitial": numf(data.get("price_overview", {}).get("initial", 0.0)) / 100.0,
        "PriceFinal": numf(data.get("price_overview", {}).get("final", 0.0)) / 100.0,
    }


def sanity_check():
    """Make sure COLUMNS and a default record match up."""
    blank = record({'query_appid': '', 'query_appname': '', 'data': {}})
    keys = set(blank.keys())
    cols = set(COLUMNS)
    if len(cols) != len(keys):
        print("Column mismatch: expected %d but found %d in blank record" % (
            len(cols), len(keys)
        ))
        print("In COLUMNS, but not in rec: %s" % repr(cols-keys))
        print("In rec, but not in COLUMNS: %s" % repr(keys-cols))
        raise Exception("Failed column check")
    if len(COLUMNS) != len(cols):
        print("Check failed: duplicate columns!")
        from collections import Counter
        print([k for k, c in Counter(COLUMNS).items() if c > 1])
        raise Exception("Duplicate columns found")


def main():
    """Entry point."""
    sanity_check()

    print("Creating games-features.csv")
    with open("games-features.csv", "w") as basefile:
        writer = csv.writer(basefile)
        writer.writerow(COLUMNS)
        count = 0
        for game in game_reader():
            rec = record(game)
            writer.writerow([rec[c] for c in COLUMNS])
            count += 1
    print("Game Records Written: %d" % count)


if __name__ == "__main__":
    main()


Creating games-features.csv
Could not int(500,000 .. 1,000,000)
Could not int(1,000,000 .. 2,000,000)
Could not int(2,000,000 .. 5,000,000)
Could not int(2,000,000 .. 5,000,000)
Could not int(500,000 .. 1,000,000)
Could not int(500,000 .. 1,000,000)
Could not int(2,000,000 .. 5,000,000)
Could not int(1,000,000 .. 2,000,000)
Could not int(2,000,000 .. 5,000,000)
Could not int(1,000,000 .. 2,000,000)
Could not int(1,000,000 .. 2,000,000)
Could not int(1,000,000 .. 2,000,000)
Could not int(2,000,000 .. 5,000,000)
Could not int(1,000,000 .. 2,000,000)
Could not int(1,000,000 .. 2,000,000)
Could not int(500,000 .. 1,000,000)
Could not int(1,000,000 .. 2,000,000)
Could not int(1,000,000 .. 2,000,000)
Could not int(2,000,000 .. 5,000,000)
Could not int(500,000 .. 1,000,000)
Game Records Written: 9680


In [11]:
%matplotlib inline
import scipy as sp
import matplotlib.pyplot as plt
import seaborn as sea
import pandas as pd

sea.set_palette("muted")

DEBUG:matplotlib:$HOME=/Users/rohitpro
DEBUG:matplotlib:CONFIGDIR=/Users/rohitpro/.matplotlib
DEBUG:matplotlib:matplotlib data path: /Users/rohitpro/opt/anaconda3/envs/mytfenv/lib/python3.7/site-packages/matplotlib/mpl-data
DEBUG:matplotlib:loaded rc file /Users/rohitpro/opt/anaconda3/envs/mytfenv/lib/python3.7/site-packages/matplotlib/mpl-data/matplotlibrc
DEBUG:matplotlib:matplotlib version 3.1.1
DEBUG:matplotlib:interactive is False
DEBUG:matplotlib:platform is darwin
DEBUG:matplotlib:loaded modules: ['sys', 'builtins', '_frozen_importlib', '_imp', '_thread', '_warnings', '_weakref', 'zipimport', '_frozen_importlib_external', '_io', 'marshal', 'posix', 'encodings', 'codecs', '_codecs', 'encodings.aliases', 'encodings.utf_8', '_signal', '__main__', 'encodings.latin_1', 'io', 'abc', '_abc', '_bootlocale', '_locale', 'site', 'os', 'stat', '_stat', 'posixpath', 'genericpath', 'os.path', '_collections_abc', '_sitebuiltins', 'types', 'importlib', 'importlib._bootstrap', 'importlib._bootst

DEBUG:matplotlib:CACHEDIR=/Users/rohitpro/.matplotlib
DEBUG:matplotlib.font_manager:Using fontManager instance from /Users/rohitpro/.matplotlib/fontlist-v310.json
DEBUG:matplotlib.pyplot:Loaded backend module://ipykernel.pylab.backend_inline version unknown.
DEBUG:matplotlib.pyplot:Loaded backend module://ipykernel.pylab.backend_inline version unknown.
DEBUG:matplotlib.pyplot:Loaded backend module://ipykernel.pylab.backend_inline version unknown.


In [12]:
data = pd.read_csv('games-features.csv')
data.head()

QueryID  ResponseID                      QueryName  \
0  1358470     1358470  Perfectly Perilous Provisions   
1  1358510     1358510              Snake In The Cube   
2  1358530     1358530                    Saint Kotar   
3  1358540     1358540                       Pink Gum   
4  1358560     1358560                Light the World   

                    ResponseName  ReleaseDate  RequiredAge  DemoCount  \
0  Perfectly Perilous Provisions         2021            0          1   
1              Snake In The Cube  Dec 17 2020            0          0   
2                    Saint Kotar     Aug 2021            0          0   
3                       Pink Gum  Jul 29 2020            0          0   
4                Light the World     Sep 2021            0          0   

   DeveloperCount  DLCCount  Metacritic  ...  \
0               1         0           0  ...   
1               1         0           0  ...   
2               1         1           0  ...   
3               1         0           0  ...   
4               1         0           0  ...   

                                         LegalNotice  \
0                                                      
1                                                      
2  (c) 2020 Red Martyr Entertainment d.o.o.. Sain...   
3                                                      
4                                                      

                                             Reviews  \
0                                                      
1                                                      
2                                                      
3  The author managed to demonstrate the meaning ...   
4                                                      

                                  SupportedLanguages  \
0         English**languages with full audio support   
1                                            English   
2  English* French Italian German Spanish - Spain...   
3  English* Spanish - Spain* French* Italian* Ger...   
4         English**languages with full audio support   

                       Website  \
0                         None   
1                         None   
2  https://www.saintkotar.com/   
3                         None   
4                         None   

                                       PCMinReqsText  \
0  Minimum:Requires a 64-bit processor and operat...   
1  Minimum:Requires a 64-bit processor and operat...   
2  Minimum:Requires a 64-bit processor and operat...   
3  Minimum:OS: Windows 10 32bitsProcessor: i5-321...   
4  Minimum:OS: Windows 7+Processor: I5 or betterM...   

                                       PCRecReqsText  \
0  Recommended:Requires a 64-bit processor and op...   
1  Recommended:Requires a 64-bit processor and op...   
2  Recommended:Requires a 64-bit processor and op...   
3                                                      
4  Recommended:OS: Windows 7+Processor: i7 or bet...   

                                    LinuxMinReqsText  \
0  Minimum:Requires a 64-bit processor and operat...   
1  Minimum:Requires a 64-bit processor and operat...   
2  Minimum:Requires a 64-bit processor and operat...   
3  Minimum:OS: Mint / Debian / Arch / ...Processo...   
4                                                      

                                    LinuxRecReqsText  \
0  Recommended:Requires a 64-bit processor and op...   
1  Recommended:Requires a 64-bit processor and op...   
2  Recommended:Requires a 64-bit processor and op...   
3                                                      
4                                                      

                                      MacMinReqsText  \
0  Minimum:Requires a 64-bit processor and operat...   
1  Minimum:Requires a 64-bit processor and operat...   
2  Minimum:Requires a 64-bit processor and operat...   
3  Minimum:OS: MAC OSX 10.11 El Capitan 64bitsPro...   
4                                                      

                               

In [13]:
data.columns

Index(['QueryID', 'ResponseID', 'QueryName', 'ResponseName', 'ReleaseDate',
       'RequiredAge', 'DemoCount', 'DeveloperCount', 'DLCCount', 'Metacritic',
       'MovieCount', 'PackageCount', 'RecommendationCount', 'PublisherCount',
       'ScreenshotCount', 'SteamSpyOwners', 'SteamSpyOwnersVariance',
       'SteamSpyPlayersEstimate', 'SteamSpyPlayersVariance',
       'AchievementCount', 'AchievementHighlightedCount', 'ControllerSupport',
       'IsFree', 'FreeVerAvail', 'PurchaseAvail', 'SubscriptionAvail',
       'PlatformWindows', 'PlatformLinux', 'PlatformMac', 'PCReqsHaveMin',
       'PCReqsHaveRec', 'LinuxReqsHaveMin', 'LinuxReqsHaveRec',
       'MacReqsHaveMin', 'MacReqsHaveRec', 'CategorySinglePlayer',
       'CategoryMultiplayer', 'CategoryCoop', 'CategoryMMO',
       'CategoryInAppPurchase', 'CategoryIncludeSrcSDK',
       'CategoryIncludeLevelEditor', 'CategoryVRSupport', 'GenreIsNonGame',
       'GenreIsIndie', 'GenreIsAction', 'GenreIsAdventure', 'GenreIsCasual',
       'G